In [1]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from pybloom import BloomFilter
import inspect

In [2]:
def generateGauss(numcompo, gap, sigma, numelepercompo):
    mu = 0
    ans = []
    for i in range(0, numcompo):
        s = np.random.normal(mu, sigma, numelepercompo)
#         print(s)
        ans += s.tolist()
        mu += gap
    return np.array([ans]).transpose()


In [113]:
def generateGaussArr(numcompo, gap, sigma, numelepercompo):
    mu = 0
    ans = []
    for i in range(0, numcompo):
        s = np.random.normal(mu, sigma, numelepercompo)
#         print(s)
        ans.append(s)
        mu += gap
    return np.array(ans)


In [259]:
from sklearn import preprocessing
import numpy as np
import sys
from sklearn.metrics import accuracy_score
import pickle
from sklearn import mixture
import math

def ngram(X, gramsize):
    numele = len(X)
    minlen = len(X[0])
    maxlen = len(X[0])
    
    for i in X:
        templen = len(i)
        if(templen>maxlen):
            maxlen=templen
        if(templen<minlen):
            minlen=templen
    reqdim = maxlen - gramsize +1
    
    Y = []
    for i in X:
        tempy = []
        paddedi = i + "0"*(maxlen-len(i))
        for j in range(0,len(paddedi)-gramsize+1):
            tempy.append(paddedi[j:j+gramsize])
        if len(tempy) == 0:
            tempy = [paddedi]
        templeny = len(tempy)
        
        Y.append(tempy)
    return Y

def ngramEnforce(X, gramsize, reqdim):
    numele = len(X)
    minlen = len(X[0])
    maxlen = len(X[0])
    for i in X:
        templen = len(i)
        if(templen>maxlen):
            maxlen=templen
        if(templen<minlen):
            minlen=templen
    maxlen = reqdim + gramsize -1
    Y = []
    for i in X:
        tempy = []
        paddedi = i + "0"*(maxlen-len(i))
        for j in range(0,len(paddedi)-gramsize+1):
            tempy.append(paddedi[j:j+gramsize])
        templeny = len(tempy)
        
        Y.append(tempy)
    return np.array(Y)

def rstripfn(x):
    x = x.rstrip('\n')
    
    return x.rstrip('\n')

def getDataInString(filename):
    with open(filename) as f1:
        lst1 = map(rstripfn,f1.readlines())
    return lst1

def findngram(gramsize, lst1):
    lst1g = ngram(lst1, gramsize)

    reqdim = len(lst1g[0])
    lst1f = []
    for i in lst1g:
        lst1f.append(map(float, i))

    nplst1 = np.array(lst1f)
    return (nplst1,reqdim)

def preprocess_train(nplst1):
    lstf1 = nplst1.astype(float)
    min_max_scaler = preprocessing.MinMaxScaler()
    lstS1 = min_max_scaler.fit_transform(lstf1)
    return lstS1, min_max_scaler

def preprocess_test(nplst1, min_max_scaler):
    lstf1 = nplst1.astype(float)
    lstS1 = min_max_scaler.transform(lstf1)
    return lstS1

def trainfn(lstS1, n_compo, maxiter):
    clf = mixture.GaussianMixture(n_components=n_compo, covariance_type='full', max_iter=maxiter)
    clf.fit(lstS1)
    return clf

def findmeansigma(clf, lstS1):
    meanscore = np.mean(clf.score_samples(lstS1))
    meanvar = np.var(clf.score_samples(lstS1))
    sigma = math.sqrt(meanvar)
    return (meanscore, sigma)

def mypred(X, clf, mean, sigma):
    scores = clf.score_samples(X)
    print(scores)
    predictions = []
    for i in scores:
        print("diff is ",abs(i-mean))
        if(abs(i-mean)<=max(thres*sigma, 1.0/1e12)):
            predictions.append(1)
        else:
            predictions.append(-1)
    return predictions

def calcncompo(n):
    if(n>10000):
        return 100
    elif(n<60):
        return max(1, n/10)
    else:
        return 9

def areAllNumeric(l):
    l1 = map(isCharacterAscii, l)
    return all(l1)

def isCharacterAscii(str):
    try:
        float(str)
        return True
    except ValueError:
        return False

def train(filename, sstableID):
    lst1 = getDataInString(filename)
    if(not areAllNumeric(lst1)):
        print("returning cause key is not numeric")
        return
    if(len(lst1) == 1):
        print('returning cause num key is 1')
        return
    nplst1, reqdim = findngram(gramsize, lst1)
    lstS1, min_max_scaler = preprocess_train(nplst1)
    n_compo = calcncompo(len(lst1))
    clf = trainfn(lstS1, n_compo, maxiter)
    mean, sigma = findmeansigma(clf, lstS1)
    models[str(sstableID)] = (clf, mean, sigma, reqdim, min_max_scaler)
    print('training done with sstableid - ', sstableID)
    return

def trainIndi(nplst1, sstableID,n_compo):
#     lst1 = getDataInString(filename)
#     if(not areAllNumeric(lst1)):
#         print("returning cause key is not numeric")
#         return
#     if(len(lst1) == 1):
#         print('returning cause num key is 1')
#         return
#     nplst1, reqdim = findngram(gramsize, lst1)
#     print("prev mean was ", np.mean(nplst1.transpose()))
#     print("prev var was ", np.var(nplst1.transpose()))
#     lstS1, min_max_scaler = preprocess_train(nplst1)
    print("passed mean was ",np.mean(nplst1.transpose()))
    print("passed sigma was ",np.var(nplst1.transpose()))
    print(nplst1)
    print(nplst1.shape)
#     n_compo = calcncompo(len(lst1))
    clf = trainfn(nplst1, n_compo, maxiter)
    print("found means ")
    print(np.sort(clf.means_.transpose()[0]))
    print("cov matrix ")
    print(clf.covariances_)
    print("weights :")
    print(clf.weights_)
    mean, sigma = findmeansigma(clf, nplst1)
    print("mean is ",str(mean))
    print("sigma is ", str(sigma))
    reqdim = len(nplst1[0])
    models[str(sstableID)] = (clf, mean, sigma, reqdim)
    print('training done with sstableid - ', sstableID)
    return

def test(keyPredstr, sstableID):
    if(keyPredstr == ''):
        print('returning cause string is empty')
        return 0
    if(not isCharacterAscii(keyPredstr)):
        print('returning cause not numric')
        return 0
    keyPred = [str(keyPredstr)]
    if sstableID in models:
        # sizeofmodels()
        clf, mean, sigma, reqdim, min_max_scaler = models[str(sstableID)]
        keyPredg = ngramEnforce(keyPred, gramsize, reqdim)
        keyPredS = preprocess_test(keyPredg, min_max_scaler)
        prediction = mypred(keyPredS, clf, mean, sigma)
        return prediction[0]
    else:
        print(str(sstableID), ' - sstableid not in models')
        return 0

    
def testIndi(keyPredg, sstableID):
#     if(keyPredstr == ''):
#         print('returning cause string is empty')
#         return 0
#     if(not isCharacterAscii(keyPredstr)):
#         print('returning cause not numric')
#         return 0
#     keyPred = [str(keyPredstr)]
    if str(sstableID) in models:
        # sizeofmodels()
        clf, mean, sigma, reqdim= models[str(sstableID)]
#         keyPredg = ngramEnforce(keyPred, gramsize, reqdim)
#         keyPredS = preprocess_test([keyPredg], min_max_scaler)
        prediction = mypred([keyPredg], clf, mean, sigma)
        return prediction[0]
    else:
        print(str(sstableID), ' - sstableid not in models')
        return 0

def testIndi2(keyPredg, sstableID):
#     if(keyPredstr == ''):
#         print('returning cause string is empty')
#         return 0
#     if(not isCharacterAscii(keyPredstr)):
#         print('returning cause not numric')
#         return 0
#     keyPred = [str(keyPredstr)]
    if str(sstableID) in models:
        # sizeofmodels()
        clf, mean, sigma, reqdim= models[str(sstableID)]
#         keyPredg = ngramEnforce(keyPred, gramsize, reqdim)
#         keyPredS = preprocess_test([keyPredg], min_max_scaler)
        prediction = mypred(keyPredg, clf, mean, sigma)
        return prediction
    else:
        print(str(sstableID), ' - sstableid not in models')
        return 0
    
def sizeofmodels():
    l = []
    for sstableID in models:
        clf, mean, sigma, reqdim, min_max_scaler = models[str(sstableID)]
        print("yo")
        print(clf)
        p = pickle.dumps(clf)
        tempsize = sys.getsizeof(p)
        # print(str(tempsize))
        # print(sys.getsizeof(p))
        print(sstableID, sys.getsizeof(p))
def sumsizeofmodels(models):
    agg =0
    for sstableID in models:
        clf, mean, sigma, reqdim= models[str(sstableID)]
        print("yo")
        print(clf)
        p = pickle.dumps(clf)
        tempsize = sys.getsizeof(p)
        agg += tempsize
        # print(str(tempsize))
        # print(sys.getsizeof(p))
        print(sstableID, sys.getsizeof(p))
    return agg
def sumsizeofbloom(bloomfilters):
    agg =0
    for f in bloomfilters.values():
        agg += f.num_bits
    agg = agg/8
    return agg




In [260]:
gramsize = -1
maxiter = 100
models = {} # storing models based on sstable ids

In [261]:
numclustersPerSStable = 10
numclustersPerSStableForTrain = numclustersPerSStable
numSstable = 30
numelePerCluster = 20
gapBetweenClusters = 0.5
clusterSigma = 0.1
ssTableData = {}



In [262]:
thres = -0.1
bloomfilters = {}
capacityBloom = 30000
errorRate = 0.1
skipFactor = 1

In [263]:
# Generate the data
alltemptableData = generateGaussArr(
    numclustersPerSStable*numSstable, gapBetweenClusters, clusterSigma, numelePerCluster )
np.random.shuffle(alltemptableData)
for i in range(0,numSstable):
    thistableData = alltemptableData[i*numclustersPerSStable:(i+1)*numclustersPerSStable].flatten()
    ssTableData[i] = thistableData.reshape(-1,1)

In [264]:
ssTableData

{0: array([[ 57.63103624],
        [ 57.31057096],
        [ 57.52386378],
        [ 57.57316575],
        [ 57.29905291],
        [ 57.50503315],
        [ 57.56839967],
        [ 57.46446441],
        [ 57.36057155],
        [ 57.34448043],
        [ 57.54349694],
        [ 57.41406445],
        [ 57.23458807],
        [ 57.34561035],
        [ 57.47423185],
        [ 57.53230275],
        [ 57.66122852],
        [ 57.58235187],
        [ 57.48810061],
        [ 57.61154739],
        [ 96.92660241],
        [ 96.70703552],
        [ 97.05380911],
        [ 96.91685295],
        [ 97.01773575],
        [ 96.86373323],
        [ 97.03360813],
        [ 96.95394633],
        [ 96.99349639],
        [ 96.96085789],
        [ 97.07439619],
        [ 96.8925206 ],
        [ 96.97886495],
        [ 96.71010364],
        [ 96.78713885],
        [ 97.08006066],
        [ 97.06147474],
        [ 97.11607478],
        [ 97.28932792],
        [ 97.09444628],
        [ 73.58539684],
        [ 73.

In [265]:
# alltemptableData

In [266]:
%%time
# train the model on generated data
for i in range(0,numSstable):
    thistableData = ssTableData[i]
    trainIndi(thistableData,i, numclustersPerSStableForTrain)


('passed mean was ', 76.29839032478517)
('passed sigma was ', 1664.1347762445353)
[[ 57.63103624]
 [ 57.31057096]
 [ 57.52386378]
 [ 57.57316575]
 [ 57.29905291]
 [ 57.50503315]
 [ 57.56839967]
 [ 57.46446441]
 [ 57.36057155]
 [ 57.34448043]
 [ 57.54349694]
 [ 57.41406445]
 [ 57.23458807]
 [ 57.34561035]
 [ 57.47423185]
 [ 57.53230275]
 [ 57.66122852]
 [ 57.58235187]
 [ 57.48810061]
 [ 57.61154739]
 [ 96.92660241]
 [ 96.70703552]
 [ 97.05380911]
 [ 96.91685295]
 [ 97.01773575]
 [ 96.86373323]
 [ 97.03360813]
 [ 96.95394633]
 [ 96.99349639]
 [ 96.96085789]
 [ 97.07439619]
 [ 96.8925206 ]
 [ 96.97886495]
 [ 96.71010364]
 [ 96.78713885]
 [ 97.08006066]
 [ 97.06147474]
 [ 97.11607478]
 [ 97.28932792]
 [ 97.09444628]
 [ 73.58539684]
 [ 73.47140554]
 [ 73.48637348]
 [ 73.64876892]
 [ 73.45638091]
 [ 73.53392262]
 [ 73.56924194]
 [ 73.49212041]
 [ 73.46162728]
 [ 73.47804777]
 [ 73.48088553]
 [ 73.55879777]
 [ 73.42728506]
 [ 73.5230865 ]
 [ 73.56858407]
 [ 73.53823306]
 [ 73.61566184]
 [ 73.

found means 
[  2.52458294   4.52112386   7.51601266  29.02498581  41.96496636
  76.51245077  98.51658209 125.97827917 131.96710153 146.51319807]
cov matrix 
[[[0.01325297]]

 [[0.00522111]]

 [[0.00619185]]

 [[0.01642792]]

 [[0.00628803]]

 [[0.00939954]]

 [[0.0061861 ]]

 [[0.00692266]]

 [[0.01069111]]

 [[0.01169388]]]
weights :
[0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1]
('mean is ', '-1.3437859579915012')
('sigma is ', '0.655812965103')
('training done with sstableid - ', 21)
('passed mean was ', 69.20063543600222)
('passed sigma was ', 1572.2476871737597)
[[ 40.5035311 ]
 [ 40.46042267]
 [ 40.35436642]
 [ 40.74193735]
 [ 40.38601278]
 [ 40.55188072]
 [ 40.4821684 ]
 [ 40.61727756]
 [ 40.49777433]
 [ 40.43044914]
 [ 40.52205556]
 [ 40.6108243 ]
 [ 40.37137806]
 [ 40.63372801]
 [ 40.58012787]
 [ 40.47228692]
 [ 40.44033452]
 [ 40.63997537]
 [ 40.60479077]
 [ 40.59595055]
 [119.4924635 ]
 [119.32360848]
 [119.39884396]
 [119.63236101]
 [119.33047583]
 [119.6941103 ]
 [119.71925127

In [254]:
%%time
# put into bloom filter false negatives
for i in range(0,numSstable):
    thistableData = ssTableData[i]
    thistableDataTranspose0 = thistableData.transpose()[0]
    falseNegativeAns = testIndi2(thistableData, i)
    numFalseNeg = falseNegativeAns.count(-1)
#     newCapacity = int(capacityBloom*1.0*numFalseNeg/len(thistableData))
    newCapacity = max(numFalseNeg,1)
    print("newCapacity ",newCapacity)
    f = BloomFilter(capacity=newCapacity, error_rate=errorRate)
    for j in range(0,len(thistableDataTranspose0)):
        if(falseNegativeAns[j]==-1):
#             print("adding ", thistableDataTranspose0[j])
            f.add(thistableDataTranspose0[j])
    bloomfilters[i] = f

[-0.97950266 -1.14091121 -1.41452917 -1.56359364 -1.95363881 -1.00773349
 -1.14945886 -1.25188926 -2.30316153 -1.27879362 -1.35502733 -0.98335461
 -1.65092644 -1.22315013 -0.98325093 -1.03689386 -1.25021276 -1.9114148
 -1.89813776 -3.22194637 -3.09221601 -2.45951411 -0.95836806 -1.16313752
 -1.75697839 -2.03178779 -0.99012908 -2.1681074  -1.47702714 -1.05659331
 -0.9596455  -0.97707733 -0.96812577 -1.29092198 -1.16672253 -1.6750541
 -1.15189105 -1.23179232 -0.9582963  -1.63161388 -4.4205431  -1.12029993
 -1.01171836 -1.47425208 -1.23338316 -1.0109243  -1.01490508 -1.22813475
 -1.10308147 -1.38213264 -1.17446758 -1.10975033 -1.29509384 -1.05544228
 -2.04300803 -1.19457233 -1.14565997 -1.31369072 -1.40654172 -3.44915885
 -1.00854993 -1.56318301 -1.1184752  -2.06677243 -1.05667151 -1.10330386
 -2.2790315  -2.11247165 -1.24847321 -1.01403644 -2.6654513  -1.3691656
 -2.00492328 -1.0256346  -1.99959041 -1.24973015 -1.29995449 -1.29497033
 -1.58467335 -1.09866488 -2.39462307 -3.16913491 -0.75

('diff is ', 0.3789403100405091)
('diff is ', 0.25071737614039)
('diff is ', 0.6527254715925215)
('diff is ', 0.5513762000348581)
('diff is ', 0.6839095661348151)
('diff is ', 0.6020929797250656)
('diff is ', 0.46606185862378857)
('diff is ', 0.04087794080797558)
('diff is ', 0.6533008642314764)
('diff is ', 0.6034727657856171)
('diff is ', 1.8757911235804963)
('diff is ', 0.641774077388716)
('diff is ', 0.05794922116465062)
('diff is ', 0.6546226745763899)
('diff is ', 0.1655996455467308)
('diff is ', 0.5358282663518354)
('diff is ', 0.6593607027232593)
('diff is ', 0.2808857146921653)
('diff is ', 0.6761358494139695)
('diff is ', 0.05923266134182925)
('diff is ', 0.19249227008618375)
('diff is ', 0.4659061978639536)
('diff is ', 0.6602535079579679)
('diff is ', 0.41780629365557886)
('diff is ', 0.5861329263931643)
('diff is ', 0.5629285942018287)
('diff is ', 0.20620135784256255)
('diff is ', 0.2015912041923389)
('diff is ', 0.03362764242543537)
('diff is ', 0.2569560289379804)
('dif

('diff is ', 0.08673823069408382)
('diff is ', 0.11506231910731257)
('diff is ', 0.12080530232202924)
('diff is ', 0.003294008861712383)
('diff is ', 0.30207451929228957)
('diff is ', 2.9597890053398475)
('diff is ', 0.08436975243266853)
('diff is ', 0.20053143532182438)
('diff is ', 0.038711790900099574)
('diff is ', 0.2658591123985399)
('diff is ', 0.2868038047737922)
('diff is ', 0.2650586612857626)
('diff is ', 0.2800496230467908)
('diff is ', 0.28470597824883614)
('diff is ', 2.2115887413422097)
('diff is ', 0.30255253885408684)
('diff is ', 0.2316611368357877)
('diff is ', 0.053982208965691614)
('diff is ', 0.23519632437787297)
('diff is ', 0.012779981246912486)
('diff is ', 0.4343860762189127)
('diff is ', 0.39527218832154287)
('diff is ', 0.5680531186914763)
('diff is ', 0.20197189786186764)
('diff is ', 1.711742954279569)
('diff is ', 0.32612514257433145)
('diff is ', 0.31689333091116145)
('diff is ', 0.43242695074256843)
('diff is ', 0.05149682719621462)
('diff is ', 0.365904

[-1.32823856 -1.48218589 -1.05965177 -2.88555542 -1.29996185 -1.1031146
 -1.04291144 -1.55306038 -2.04525999 -1.18141634 -1.01573805 -1.64110993
 -1.47456597 -1.22999979 -1.09760327 -1.61397905 -1.03352355 -2.09316784
 -2.27573848 -1.85555995 -1.85021416 -1.00255525 -1.07824525 -1.08557386
 -1.00101684 -2.64999966 -1.0462429  -2.1327661  -0.99655323 -1.19711867
 -0.99509031 -1.52943833 -1.67161346 -1.27342119 -1.26788713 -2.12558121
 -1.11094399 -0.98955575 -1.46000176 -3.32606196 -1.55645431 -0.90262697
 -0.94341782 -2.65388047 -0.99284401 -1.24578247 -1.21723766 -0.94038754
 -1.54743825 -0.89414379 -1.83748994 -1.27830025 -1.79087665 -0.89191393
 -0.93360268 -1.36564651 -1.88946078 -1.11923359 -2.56484475 -0.9060451
 -1.10847487 -1.82027237 -1.18031307 -1.45465694 -1.52706969 -2.86324192
 -1.10486921 -1.20164544 -1.15316918 -2.03954208 -1.89545312 -2.29295985
 -1.56860615 -1.30888109 -1.19296082 -1.10740466 -1.73278329 -1.10805259
 -1.72385193 -2.01714085 -0.74961693 -0.66457134 -1.0

[-1.23979835 -1.80393186 -1.09638163 -1.39961466 -2.43734505 -1.0951302
 -1.07399691 -2.14277344 -1.07787416 -3.11237253 -1.08599212 -1.1472734
 -1.11177755 -1.92709584 -1.08553293 -1.07702967 -2.41549556 -1.75826665
 -1.08365541 -2.26630665 -1.07346778 -1.26765717 -1.06785713 -1.55133283
 -1.21221901 -2.01521505 -1.07210204 -1.61531646 -1.1993218  -3.02391913
 -1.0983448  -2.02000064 -1.44827452 -1.0812772  -1.07076098 -1.58906539
 -1.29392992 -3.89344697 -1.4112003  -1.35062838 -0.85730461 -1.06528334
 -0.94313336 -0.80320686 -0.89889814 -1.4727524  -1.11524453 -1.3667844
 -0.9337041  -0.90163663 -2.20999893 -1.21723244 -1.0405471  -2.19950217
 -1.0568112  -1.30071194 -0.83516495 -1.59026006 -1.81291074 -1.87018829
 -1.10796713 -2.23930833 -1.43499895 -1.2553467  -2.11710782 -0.99141655
 -1.79680133 -0.73371587 -1.00993899 -1.88902418 -0.92932661 -1.00294913
 -0.81852488 -0.81282902 -0.7277142  -1.06909347 -1.18584527 -1.50048174
 -0.73663646 -1.19298466 -0.95488319 -0.93228808 -0.93

In [255]:
%%time
# create test data
# For now test data is all data
# calculate false positives for test data
truePositive_c=0
truePositive_bf=0
truePositive=0
falsePositive_c=0
falsePositive_bf=0
falsePositive=0
trueNegative=0
for i in range(0, numSstable):
    print("on sstable number ", i)
    thistableData = ssTableData[i]
    thistableDataTranspose0 = thistableData.transpose()[0]
    for elemind in range(0,len(thistableDataTranspose0),skipFactor):
        elem = thistableDataTranspose0[elemind]
        for j in range(0,numSstable):
            cAnswer = (testIndi([elem],j)==1)
            print(cAnswer)
            if not cAnswer:
                bfAnswer = elem in bloomfilters[j]
                finAnswer = bfAnswer
            else:
                bfAnswer = None
                finAnswer = cAnswer
            if finAnswer:
                if(i==j):
                    #True answer true positive
                    #break because you found answer
                    truePositive+=1
                    if bfAnswer is None:
                        truePositive_c+=1
                    else:
                        truePositive_bf+=1
                    break
                else:
                    #False answer false positive
                    falsePositive+=1
                    if bfAnswer is None:
                        falsePositive_c+=1
                    else:
                        falsePositive_bf+=1
            else:
                if(i==j):
                    raise ValueEroor("not possible")
                else:
                    #True answer true negative
                    trueNegative+=1
                
        


('on sstable number ', 0)
[-0.97950266]
('diff is ', 0.4644909094959322)
False
[-1.14091121]
('diff is ', 0.3030823634264759)
False
[-1.41452917]
('diff is ', 0.02946440205596823)
False
[-1.56359364]
('diff is ', 0.1196000686200629)
False
[-1.95363881]
('diff is ', 0.5096452321852685)
False
[-1.00773349]
('diff is ', 0.436260086018615)
False
[-1.14945886]
('diff is ', 0.2945347096351705)
False
[-1.25188926]
('diff is ', 0.19210431497768554)
False
[-2.30316153]
('diff is ', 0.859167961628809)
False
[-1.27879362]
('diff is ', 0.16519994823388684)
False
[-1.35502733]
('diff is ', 0.08896624290692712)
False
[-0.98335461]
('diff is ', 0.4606389618773705)
False
[-1.65092644]
('diff is ', 0.20693286750330375)
False
[-1.22315013]
('diff is ', 0.2208434421401042)
False
[-0.98325093]
('diff is ', 0.4607426410278703)
False
[-1.03689386]
('diff is ', 0.4070997129082625)
False
[-1.25021276]
('diff is ', 0.19378081422064652)
False
[-1.9114148]
('diff is ', 0.4674212264587505)
False
[-1.89813776]
('d

[-0.99014594]
('diff is ', 0.36989412716174064)
False
[-2379.80217209]
('diff is ', 2378.3581785196307)
False
[-2.13704237]
('diff is ', 0.7770023035669351)
False
[-2329.78940113]
('diff is ', 2328.345407558096)
False
[-1.23483356]
('diff is ', 0.1252065057736773)
False
[-2214.14991395]
('diff is ', 2212.705920376458)
False
[-1.70095312]
('diff is ', 0.3409130518597592)
False
[-2338.41196603]
('diff is ', 2336.967972452463)
False
[-1.34410179]
('diff is ', 0.015938280676930372)
False
[-2281.98026205]
('diff is ', 2280.5362684737756)
False
[-0.98625213]
('diff is ', 0.37378794081878475)
False
[-2214.13347052]
('diff is ', 2212.689476944737)
False
[-1.70128212]
('diff is ', 0.3412420502348015)
False
[-313.43173625]
('diff is ', 311.9877426719829)
False
[-1.88330987]
('diff is ', 0.5232697997674101)
False
[-290.68066633]
('diff is ', 289.236672758727)
False
[-1.05464664]
('diff is ', 0.3053934306788997)
False
[-320.93190325]
('diff is ', 319.487909680661)
False
[-2.33627937]
('diff is ', 

False
[-6224.57680661]
('diff is ', 6223.216766542085)
False
[-0.94280566]
('diff is ', 0.44972630617315845)
False
[-408.71671352]
('diff is ', 407.2727199446108)
False
[-6257.58376853]
('diff is ', 6256.22372845743)
False
[-0.99822001]
('diff is ', 0.3943119549688874)
False
[-413.33141886]
('diff is ', 411.8874252913312)
False
[-6240.1158958]
('diff is ', 6238.755855730961)
False
[-0.95688484]
('diff is ', 0.4356471294204798)
False
[-452.42279439]
('diff is ', 450.97880081672014)
False
[-6096.83334313]
('diff is ', 6095.47330306443)
False
[-1.64743327]
('diff is ', 0.25490130343186745)
False
[-399.21074128]
('diff is ', 397.766747705084)
False
[-6293.95877421]
('diff is ', 6292.598734139796)
False
[-1.17046713]
('diff is ', 0.2220648312696054)
False
[-408.88030319]
('diff is ', 407.4363096128501)
False
[-6256.96243526]
('diff is ', 6255.602395186636)
False
[-0.99628782]
('diff is ', 0.39624414825641807)
False
[-468.40856443]
('diff is ', 466.96457085914903)
False
[-6040.49647684]
('di

[-2377.38763104]
('diff is ', 2375.943637466796)
False
[-52.40540552]
('diff is ', 51.045365449364844)
False
[-1.21670496]
('diff is ', 0.17582700865853118)
False
[-2375.8290489]
('diff is ', 2374.385055328888)
False
[-52.18083233]
('diff is ', 50.82079225658348)
False
[-1.19067155]
('diff is ', 0.2018604182035464)
False
[-2328.12150527]
('diff is ', 2326.67751169276)
False
[-45.51115496]
('diff is ', 44.151114887399984)
False
[-0.78250814]
('diff is ', 0.6100238281352719)
False
[-2337.60462029]
('diff is ', 2336.160626712804)
False
[-46.80513357]
('diff is ', 45.44509350020428)
False
[-0.80318395]
('diff is ', 0.5893480114889251)
False
[-2381.7565619]
('diff is ', 2380.312568329431)
False
[-53.03714344]
('diff is ', 51.67710336894396)
False
[-1.29391484]
('diff is ', 0.09861712727380478)
False
[-2272.39437187]
('diff is ', 2270.9503783018135)
False
[-38.23304386]
('diff is ', 36.87300378735179)
False
[-1.28073306]
('diff is ', 0.11179890784581414)
False
[-2317.28738537]
('diff is ', 2

[-10.79028471]
('diff is ', 9.397752740446332)
False
[-0.85935702]
('diff is ', 0.5258907043704855)
False
[-12815.53417008]
('diff is ', 12814.0901765034)
False
[-9495.57530528]
('diff is ', 9494.21526520622)
False
[-10.7828307]
('diff is ', 9.39029872950063)
False
[-0.85991022]
('diff is ', 0.5253375059981893)
False
[-12681.83866908]
('diff is ', 12680.394675509006)
False
[-9379.39247107]
('diff is ', 9378.032431004562)
False
[-7.5502406]
('diff is ', 6.157708631428778)
False
[-1.60261004]
('diff is ', 0.21736231674850037)
False
[-12787.18592313]
('diff is ', 12785.741929557907)
False
[-9470.93153289]
('diff is ', 9469.571492819838)
False
[-10.04480175]
('diff is ', 8.652269779908577)
False
[-0.93737038]
('diff is ', 0.4478773448834017)
False
[-12745.88172932]
('diff is ', 12744.43773574864)
False
[-9435.03335702]
('diff is ', 9433.673316952081)
False
[-9.02002102]
('diff is ', 7.6274890508113105)
False
[-1.12712407]
('diff is ', 0.25812365966173667)
False
[-12876.9546632]
('diff is '

...

[-20.63673021]
('diff is ', 19.244198240394386)
False
[-5768.26422803]
('diff is ', 5766.878980308269)
False
[-144.12155667]
('diff is ', 142.83990112642857)
False
[-33.28508934]
('diff is ', 31.91545076024796)
False
[-100.70492418]
('diff is ', 99.32031825654902)
False
[-3646.10071761]
('diff is ', 3644.806806342718)
False
[-115.1950905]
('diff is ', 113.79274916686256)
False
[-608.70092231]
('diff is ', 607.3389209801148)
False
[-676.4884877]
('diff is ', 675.2104846937939)
False
[-8938.41102758]
('diff is ', 8937.00918404313)
False
[-252.19440453]
('diff is ', 250.7602194436718)
False
[-5473.03828052]
('diff is ', 5471.6986935074065)
False
[-37372.98097436]
('diff is ', 37371.668375681256)
False
[-397.97837458]
('diff is ', 396.636093724354)
False
[-2744.90245051]
('diff is ', 2743.5269240886983)
False
[-1224.71089161]
('diff is ', 1223.358758787012)
False
[-7.62387081]
('diff is ', 6.232638350505919)
False
[-4006.14850971]
('diff is ', 4004.865580769032)
False
[-18416.28524208]
('d

[-6546.72444601]
('diff is ', 6545.383873291972)
False
[-4468.80260055]
('diff is ', 4467.447519815924)
False
[-265.05630981]
('diff is ', 263.605246461294)
False
[-5460.14872723]
('diff is ', 5458.782068009848)
False
[-12300.72092379]
('diff is ', 12299.309180831537)
False
[-3.05162319]
('diff is ', 1.61057841953607)
False
[-19330.58635353]
('diff is ', 19329.142359961203)
False
[-9163.65088401]
('diff is ', 9162.290843935674)
False
[-9873.97113272]
('diff is ', 9872.578600750834)
False
[-1412.90414802]
('diff is ', 1411.5189002918491)
False
[-15560.61699771]
('diff is ', 15559.335342167185)
False
[-21.82637648]
('diff is ', 20.456737904689064)
False
[-1214.97966895]
('diff is ', 1213.5950630227335)
False
[-76.08318592]
('diff is ', 74.78927464516164)
False
[-201.77224985]
('diff is ', 200.3699085091867)
False
[-46826.49198915]
('diff is ', 46825.12998781659)
False
[-56030.32360465]
('diff is ', 56029.04560163885)
False
[-123.52017639]
('diff is ', 122.11833285669304)
False
[-9.758918

[-359.35218025]
('diff is ', 357.9539620268982)
False
[-317.78561306]
('diff is ', 316.4345393443456)
False
[-6181.86886433]
('diff is ', 6180.528291612609)
False
[-4757.80078501]
('diff is ', 4756.445704282128)
False
[-212.75905595]
('diff is ', 211.30799259905976)
False
[-5687.45770197]
('diff is ', 5686.091042748088)
False
[-12633.90159004]
('diff is ', 12632.48984708603)
False
[-0.96855274]
('diff is ', 0.47249202371933285)
False
[-19264.66642707]
('diff is ', 19263.222433501684)
False
[-9119.15086168]
('diff is ', 9117.790821607676)
False
[-9830.10034537]
('diff is ', 9828.707813399533)
False
[-1394.21281068]
('diff is ', 1392.8275629592824)
False
[-15482.18142455]
('diff is ', 15480.899769014084)
False
[-18.97192449]
('diff is ', 17.602285910833615)
False
[-1235.12721638]
('diff is ', 1233.7426104565175)
False
[-81.91834684]
('diff is ', 80.62443556716912)
False
[-194.59352542]
('diff is ', 193.19118407819715)
False
[-46686.53196407]
('diff is ', 46685.16996273837)
False
[-55919.

[-20030.55945185]
('diff is ', 20029.246853173627)
False
[-434.94019293]
('diff is ', 433.5979120712302)
False
[-53.28673418]
('diff is ', 51.91120775035591)
False
[-951.62456074]
('diff is ', 950.2724279182781)
False
[-1644.68616675]
('diff is ', 1643.2949342891443)
False
[-5061.7589114]
('diff is ', 5060.475982461054)
False
[-7531.42532308]
('diff is ', 7530.001249180893)
False
[-12129.42535861]
('diff is ', 12128.057008175441)
False
[-13280.82659115]
('diff is ', 13279.428372923036)
False
[-4688.55346633]
('diff is ', 4687.202392611616)
False
[-64.59832125]
('diff is ', 63.257748530306266)
False
[-26611.75692561]
('diff is ', 26610.40184487659)
False
[-106.02600042]
('diff is ', 104.57493706649149)
False
[-6880.77261867]
('diff is ', 6879.405959442286)
False
[-158.47126329]
('diff is ', 157.05952033200745)
False
[-1.04884161]
('diff is ', 0.39220315737150124)
False
[-121.20299276]
('diff is ', 119.75899918427749)
False
[-272.20032248]
('diff is ', 270.84028240642965)
False
[-4308.74

[-288.06897759]
('diff is ', 286.7089375242034)
False
[-4237.34158304]
('diff is ', 4235.9490510738)
False
[-1010.31616228]
('diff is ', 1008.930914552469)
False
[-4991.49353892]
('diff is ', 4990.211883380857)
False
[-1582.81278401]
('diff is ', 1581.443145428558)
False
[-257.52071123]
('diff is ', 256.136105307346)
False
[-283.19994732]
('diff is ', 281.906036053046)
False
[-8.72183065]
('diff is ', 7.319489312578414)
False
[-5818.98664557]
('diff is ', 5817.624644233423)
False
[-17.13558757]
('diff is ', 15.857584558758282)
False
[-11810.00011285]
('diff is ', 11808.598269315913)
False
[-5283.99808186]
('diff is ', 5282.563896769504)
False
[-608.45683039]
('diff is ', 607.1172433766194)
False
[-19646.32812814]
('diff is ', 19645.015529460597)
False
[-481.89356001]
('diff is ', 480.55127914886333)
False
[-73.03658518]
('diff is ', 71.66105875450316)
False
[-1038.93246809]
('diff is ', 1037.580335260692)
False
[-1719.00366278]
('diff is ', 1717.6124303222214)
False
[-4891.22686106]
('

In [256]:
print(truePositive,falsePositive,trueNegative)

(6000, 1175, 85825)


In [257]:
print(truePositive_c,truePositive_bf,falsePositive_c,falsePositive_bf)

(0, 6000, 0, 1175)


In [258]:
fprate = falsePositive*1.0/(falsePositive+trueNegative)
print(fprate)

0.0135057471264


In [151]:
sumsizeofmodels(models)

yo
GaussianMixture(covariance_type='full', init_params='kmeans', max_iter=100,
        means_init=None, n_components=100, n_init=1, precisions_init=None,
        random_state=None, reg_covar=1e-06, tol=0.001, verbose=0,
        verbose_interval=10, warm_start=False, weights_init=None)
('1', 13639)
yo
GaussianMixture(covariance_type='full', init_params='kmeans', max_iter=100,
        means_init=None, n_components=100, n_init=1, precisions_init=None,
        random_state=None, reg_covar=1e-06, tol=0.001, verbose=0,
        verbose_interval=10, warm_start=False, weights_init=None)
('0', 13567)


27206

In [ ]:
sumsizeofbloom(bloomfilters)

In [ ]:
sys.getsizeof(models['0'])

In [ ]:
def get_size(obj, seen=None):
    """Recursively finds size of objects"""
    size = sys.getsizeof(obj)
    if seen is None:
        seen = set()
    obj_id = id(obj)
    if obj_id in seen:
        return 0
    # Important mark as seen *before* entering recursion to gracefully handle
    # self-referential objects
    seen.add(obj_id)
    if isinstance(obj, dict):
        size += sum([get_size(v, seen) for v in obj.values()])
        size += sum([get_size(k, seen) for k in obj.keys()])
    elif hasattr(obj, '__dict__'):
        size += get_size(obj.__dict__, seen)
    elif hasattr(obj, '__iter__') and not isinstance(obj, (str, bytes, bytearray)):
        size += sum([get_size(i, seen) for i in obj])
    else:
        print(type(obj))
        print("cases left")
    return size

In [ ]:
import sys
from types import ModuleType, FunctionType
from gc import get_referents

# Custom objects know their class.
# Function objects seem to know way too much, including modules.
# Exclude modules as well.
BLACKLIST = type, ModuleType, FunctionType


def getsize(obj):
    """sum size of object & members."""
    if isinstance(obj, BLACKLIST):
        raise TypeError('getsize() does not take argument of type: '+ str(type(obj)))
    seen_ids = set()
    size = 0
    objects = [obj]
    while objects:
        need_referents = []
        for obj in objects:
            if not isinstance(obj, BLACKLIST) and id(obj) not in seen_ids:
                seen_ids.add(id(obj))
                print(type(obj))
                print(sys.getsizeof(obj))
                size += sys.getsizeof(obj)
                print(size)
                need_referents.append(obj)
        objects = get_referents(*need_referents)
    return size

In [ ]:
getsize(models['0'][0].weights_)

In [ ]:
models['0'][0].covariances_.shape

In [ ]:
type(models['0'][0].weights_[0])

In [ ]:
tempint = 0
get_size(tempint)

In [ ]:
inspect.getmembers(models['0'][0].means_, lambda a:not(inspect.isroutine(a)))

In [ ]:
attributes = inspect.getmembers(models['0'][0], lambda a:not(inspect.isroutine(a)))

In [ ]:
[a for a in attributes if not(a[0].startswith('__') and a[0].endswith('__'))]